In [1]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import copy
import joblib

In [2]:
from py.utils import verifyDir

In [3]:
DATA_PATH = "data/PlacePulse_2/"

QSCORE_PATH = f"{DATA_PATH}/Qscores/all/Summaries/"
MAIN_OUT_PATH = "outputs/"
CACHE_PATH = f"{MAIN_OUT_PATH}/cache/"

In [4]:
verifyDir(CACHE_PATH)

### Generating samples 

In [5]:
data_dict = joblib.load(f"{MAIN_OUT_PATH}/static/data.joblib")
data_dict.keys()

dict_keys(['id', 'images', 'features', 'safety', 'label', 'path'])

In [6]:
y = np.array(data_dict["safety"]).copy()
X = np.array(data_dict["features"]).copy()
X.shape, y.shape

((3659, 22), (3659,))

### Standard Scaler

In [7]:
from sklearn.preprocessing import StandardScaler

In [8]:
scaler = StandardScaler()

In [9]:
from sklearn.preprocessing import Normalizer

In [10]:
normalizer = Normalizer()

### Classifiers

In [11]:
from sklearn.svm import SVR, LinearSVR
from sklearn.linear_model import Ridge, LinearRegression, Lasso
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor

In [12]:
regularizer_value = np.logspace(-3, 3, num=7)
type_scaler = ['passthrough', scaler, normalizer]
# dim_reductor = [t_svd, pca, sparse_pca]
random_state = 42
max_iter=2000

In [13]:
lr = LinearRegression()

param_lr = {}
param_lr['scaler'] = copy.deepcopy(type_scaler)
#param_lr['dim_reductor'] = copy.deepcopy(dim_reductor)
param_lr['regressor'] = [lr]

In [14]:
lasso = Lasso(
    tol=1e-3,
    random_state=random_state,
    max_iter=max_iter,
)

param_lasso = {}
param_lasso['scaler'] = copy.deepcopy(type_scaler)
# param_ridge['dim_reductor'] = copy.deepcopy(dim_reductor)
param_lasso['regressor__alpha'] = copy.deepcopy(regularizer_value)
param_lasso['regressor'] = [lasso]

In [15]:
ridge = Ridge(
    tol=1e-3,
    random_state=random_state,
    max_iter=max_iter,
)

param_ridge = {}
param_ridge['scaler'] = copy.deepcopy(type_scaler)
# param_ridge['dim_reductor'] = copy.deepcopy(dim_reductor)
param_ridge['regressor__alpha'] = copy.deepcopy(regularizer_value)
param_ridge['regressor'] = [ridge]

In [16]:
linear_svm = LinearSVR(
    tol=1e-3,
    random_state=random_state,
    max_iter=max_iter,
)

param_linear_svm = {}
param_linear_svm['scaler'] = copy.deepcopy(type_scaler)
# param_linear_svm['dim_reductor'] = copy.deepcopy(dim_reductor)
param_linear_svm['regressor__C'] = copy.deepcopy(regularizer_value)
param_linear_svm['regressor__loss'] = ["epsilon_insensitive", "squared_epsilon_insensitive"]
param_linear_svm['regressor'] = [linear_svm]

In [17]:
svm = SVR(
    tol=1e-3,
    max_iter=max_iter,
)

param_svm = {}
param_svm['scaler'] = copy.deepcopy(type_scaler)
# param_linear_svm['dim_reductor'] = copy.deepcopy(dim_reductor)
param_svm['regressor__C'] = copy.deepcopy(regularizer_value)
param_svm['regressor__gamma'] = ["scale", "auto"]
param_svm['regressor__kernel'] = ["linear", "poly", "rbf"]
param_svm['regressor'] = [svm]

In [18]:
ds_tree = DecisionTreeRegressor(random_state=random_state)

param_tree = {}
param_tree["scaler"] = copy.deepcopy(type_scaler)
param_tree['regressor__max_features'] = [None, 'sqrt']
param_tree['regressor__max_depth'] = np.append(None, np.arange(10, 110, 10) )
param_tree['regressor__min_samples_split'] = np.arange(3, 7)
param_tree['regressor__min_samples_leaf'] = np.arange(3, 7)
param_tree['regressor__criterion'] = ["squared_error", "friedman_mse", "absolute_error", "poisson"]
param_tree['regressor'] = [ds_tree]

### Create Pipeline

In [19]:
from joblib import Memory

In [20]:
memory = Memory(
    location=CACHE_PATH,
    # verbose=1,
)

In [21]:
from sklearn.pipeline import Pipeline

In [22]:
pipeline = Pipeline(
    steps = [
        # 1. Scaler
        ('scaler', scaler),
        # 3. Model selecction
        ('regressor', lr),
    ],
    memory=memory,
)

### Metrics

In [23]:
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score, make_scorer
from scipy.stats import pearsonr

In [24]:
def adj_r2(estimator, X, y_true):
    n, p = X.shape
    pred = estimator.predict(X)
    return 1 - ((1 - r2_score(y_true, pred)) * (n - 1))/(n-p-1)

### Create GridSearch

In [25]:
from sklearn.model_selection import GridSearchCV

In [26]:
param_grid = [param_lr, 
              param_lasso,
              param_ridge,
              param_linear_svm,
              param_svm,
              param_tree,
             ]

In [27]:
param_grid

[{'scaler': ['passthrough', StandardScaler(), Normalizer()],
  'regressor': [LinearRegression()]},
 {'scaler': ['passthrough', StandardScaler(), Normalizer()],
  'regressor__alpha': array([1.e-03, 1.e-02, 1.e-01, 1.e+00, 1.e+01, 1.e+02, 1.e+03]),
  'regressor': [Lasso(max_iter=2000, random_state=42, tol=0.001)]},
 {'scaler': ['passthrough', StandardScaler(), Normalizer()],
  'regressor__alpha': array([1.e-03, 1.e-02, 1.e-01, 1.e+00, 1.e+01, 1.e+02, 1.e+03]),
  'regressor': [Ridge(max_iter=2000, random_state=42, tol=0.001)]},
 {'scaler': ['passthrough', StandardScaler(), Normalizer()],
  'regressor__C': array([1.e-03, 1.e-02, 1.e-01, 1.e+00, 1.e+01, 1.e+02, 1.e+03]),
  'regressor__loss': ['epsilon_insensitive', 'squared_epsilon_insensitive'],
  'regressor': [LinearSVR(max_iter=2000, random_state=42, tol=0.001)]},
 {'scaler': ['passthrough', StandardScaler(), Normalizer()],
  'regressor__C': array([1.e-03, 1.e-02, 1.e-01, 1.e+00, 1.e+01, 1.e+02, 1.e+03]),
  'regressor__gamma': ['scale', 

In [28]:
grid_search = GridSearchCV(
            estimator=pipeline,
            param_grid=param_grid,
            scoring=make_scorer(r2_score),
            refit=True,
            cv=5,  # << Use time series
            verbose=4,
)

In [29]:
grid_search

GridSearchCV(cv=5,
             estimator=Pipeline(memory=Memory(location=outputs//cache/joblib),
                                steps=[('scaler', StandardScaler()),
                                       ('regressor', LinearRegression())]),
             param_grid=[{'regressor': [LinearRegression()],
                          'scaler': ['passthrough', StandardScaler(),
                                     Normalizer()]},
                         {'regressor': [Lasso(max_iter=2000, random_state=42,
                                              tol=0.001)],
                          'regressor__alpha': array([1.e-03,...
                                                   'friedman_mse',
                                                   'absolute_error',
                                                   'poisson'],
                          'regressor__max_depth': array([None, 10, 20, 30, 40, 50, 60, 70, 80, 90, 100], dtype=object),
                          'regressor__max_features': [None, 'sqrt'],
                          'regressor__min_samples_leaf': array([3, 4, 5, 6]),
                          'regressor__min_samples_split': array([3, 4, 5, 6]),
                          'scaler': ['passthrough', StandardScaler(),
                                     Normalizer()]}],
             scoring=make_scorer(r2_score), verbose=4)

### Data Split

In [30]:
from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split

In [31]:
xtrain, xtest, ytrain, ytest = train_test_split(X, 
                                                y, 
                                                train_size=0.8, 
                                                random_state=random_state,
                                               )
print(xtrain.shape, ytrain.shape, xtest.shape, ytest.shape)

(2927, 22) (2927,) (732, 22) (732,)


### Training

In [32]:
%%time
grid_search.fit(xtrain, ytrain)

Fitting 5 folds for each of 4437 candidates, totalling 22185 fits
[CV 1/5] END regressor=LinearRegression(), scaler=passthrough;, score=0.041 total time=   0.0s
[CV 2/5] END regressor=LinearRegression(), scaler=passthrough;, score=0.103 total time=   0.0s
[CV 3/5] END regressor=LinearRegression(), scaler=passthrough;, score=0.042 total time=   0.0s
[CV 4/5] END regressor=LinearRegression(), scaler=passthrough;, score=0.036 total time=   0.0s
[CV 5/5] END regressor=LinearRegression(), scaler=passthrough;, score=0.096 total time=   0.0s
________________________________________________________________________________
[Memory] Calling sklearn.pipeline._fit_transform_one...
_fit_transform_one(StandardScaler(), array([[0.000000e+00, ..., 1.017253e-03],
       ...,
       [4.208679e+01, ..., 0.000000e+00]]), 
array([0.457822, ..., 0.424183]), None, message_clsname='Pipeline', message=None)
________________________________________________fit_transform_one - 0.0s, 0.0min
[CV 1/5] END regressor=

[CV 2/5] END regressor=Lasso(max_iter=2000, random_state=42, tol=0.001), regressor__alpha=0.01, scaler=Normalizer();, score=-0.018 total time=   0.0s
[CV 3/5] END regressor=Lasso(max_iter=2000, random_state=42, tol=0.001), regressor__alpha=0.01, scaler=Normalizer();, score=-0.003 total time=   0.0s
[CV 4/5] END regressor=Lasso(max_iter=2000, random_state=42, tol=0.001), regressor__alpha=0.01, scaler=Normalizer();, score=-0.001 total time=   0.0s
[CV 5/5] END regressor=Lasso(max_iter=2000, random_state=42, tol=0.001), regressor__alpha=0.01, scaler=Normalizer();, score=-0.006 total time=   0.0s
[CV 1/5] END regressor=Lasso(max_iter=2000, random_state=42, tol=0.001), regressor__alpha=0.1, scaler=passthrough;, score=0.035 total time=   0.0s
[CV 2/5] END regressor=Lasso(max_iter=2000, random_state=42, tol=0.001), regressor__alpha=0.1, scaler=passthrough;, score=0.024 total time=   0.0s
[CV 3/5] END regressor=Lasso(max_iter=2000, random_state=42, tol=0.001), regressor__alpha=0.1, scaler=pass

[CV 3/5] END regressor=Ridge(max_iter=2000, random_state=42, tol=0.001), regressor__alpha=0.01, scaler=Normalizer();, score=0.042 total time=   0.0s
[CV 4/5] END regressor=Ridge(max_iter=2000, random_state=42, tol=0.001), regressor__alpha=0.01, scaler=Normalizer();, score=0.039 total time=   0.0s
[CV 5/5] END regressor=Ridge(max_iter=2000, random_state=42, tol=0.001), regressor__alpha=0.01, scaler=Normalizer();, score=0.096 total time=   0.0s
[CV 1/5] END regressor=Ridge(max_iter=2000, random_state=42, tol=0.001), regressor__alpha=0.1, scaler=passthrough;, score=0.041 total time=   0.0s
[CV 2/5] END regressor=Ridge(max_iter=2000, random_state=42, tol=0.001), regressor__alpha=0.1, scaler=passthrough;, score=0.103 total time=   0.0s
[CV 3/5] END regressor=Ridge(max_iter=2000, random_state=42, tol=0.001), regressor__alpha=0.1, scaler=passthrough;, score=0.042 total time=   0.0s
[CV 4/5] END regressor=Ridge(max_iter=2000, random_state=42, tol=0.001), regressor__alpha=0.1, scaler=passthroug

[CV 2/5] END regressor=LinearSVR(max_iter=2000, random_state=42, tol=0.001), regressor__C=0.001, regressor__loss=epsilon_insensitive, scaler=passthrough;, score=0.050 total time=   0.0s
[CV 3/5] END regressor=LinearSVR(max_iter=2000, random_state=42, tol=0.001), regressor__C=0.001, regressor__loss=epsilon_insensitive, scaler=passthrough;, score=-0.007 total time=   0.0s
[CV 4/5] END regressor=LinearSVR(max_iter=2000, random_state=42, tol=0.001), regressor__C=0.001, regressor__loss=epsilon_insensitive, scaler=passthrough;, score=-0.005 total time=   0.0s
[CV 5/5] END regressor=LinearSVR(max_iter=2000, random_state=42, tol=0.001), regressor__C=0.001, regressor__loss=epsilon_insensitive, scaler=passthrough;, score=0.051 total time=   0.0s
[CV 1/5] END regressor=LinearSVR(max_iter=2000, random_state=42, tol=0.001), regressor__C=0.001, regressor__loss=epsilon_insensitive, scaler=StandardScaler();, score=0.017 total time=   0.0s
[CV 2/5] END regressor=LinearSVR(max_iter=2000, random_state=42

/home/felipe/anaconda3/envs/server_PlacePulse/lib/python3.8/site-packages/sklearn/svm/_base.py:1244: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/home/felipe/anaconda3/envs/server_PlacePulse/lib/python3.8/site-packages/sklearn/svm/_base.py:1244: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/home/felipe/anaconda3/envs/server_PlacePulse/lib/python3.8/site-packages/sklearn/svm/_base.py:1244: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(


...

[CV 3/5] END regressor=DecisionTreeRegressor(random_state=42), regressor__criterion=poisson, regressor__max_depth=100, regressor__max_features=sqrt, regressor__min_samples_leaf=5, regressor__min_samples_split=3, scaler=StandardScaler();, score=-0.435 total time=   0.0s
[CV 4/5] END regressor=DecisionTreeRegressor(random_state=42), regressor__criterion=poisson, regressor__max_depth=100, regressor__max_features=sqrt, regressor__min_samples_leaf=5, regressor__min_samples_split=3, scaler=StandardScaler();, score=-0.365 total time=   0.0s
[CV 5/5] END regressor=DecisionTreeRegressor(random_state=42), regressor__criterion=poisson, regressor__max_depth=100, regressor__max_features=sqrt, regressor__min_samples_leaf=5, regressor__min_samples_split=3, scaler=StandardScaler();, score=-0.301 total time=   0.0s
[CV 1/5] END regressor=DecisionTreeRegressor(random_state=42), regressor__criterion=poisson, regressor__max_depth=100, regressor__max_features=sqrt, regressor__min_samples_leaf=5, regressor_

[CV 2/5] END regressor=DecisionTreeRegressor(random_state=42), regressor__criterion=poisson, regressor__max_depth=100, regressor__max_features=sqrt, regressor__min_samples_leaf=5, regressor__min_samples_split=5, scaler=Normalizer();, score=-0.277 total time=   0.0s
[CV 3/5] END regressor=DecisionTreeRegressor(random_state=42), regressor__criterion=poisson, regressor__max_depth=100, regressor__max_features=sqrt, regressor__min_samples_leaf=5, regressor__min_samples_split=5, scaler=Normalizer();, score=-0.388 total time=   0.0s
[CV 4/5] END regressor=DecisionTreeRegressor(random_state=42), regressor__criterion=poisson, regressor__max_depth=100, regressor__max_features=sqrt, regressor__min_samples_leaf=5, regressor__min_samples_split=5, scaler=Normalizer();, score=-0.381 total time=   0.0s
[CV 5/5] END regressor=DecisionTreeRegressor(random_state=42), regressor__criterion=poisson, regressor__max_depth=100, regressor__max_features=sqrt, regressor__min_samples_leaf=5, regressor__min_samples

[CV 2/5] END regressor=DecisionTreeRegressor(random_state=42), regressor__criterion=poisson, regressor__max_depth=100, regressor__max_features=sqrt, regressor__min_samples_leaf=6, regressor__min_samples_split=4, scaler=passthrough;, score=-0.296 total time=   0.0s
[CV 3/5] END regressor=DecisionTreeRegressor(random_state=42), regressor__criterion=poisson, regressor__max_depth=100, regressor__max_features=sqrt, regressor__min_samples_leaf=6, regressor__min_samples_split=4, scaler=passthrough;, score=-0.266 total time=   0.0s
[CV 4/5] END regressor=DecisionTreeRegressor(random_state=42), regressor__criterion=poisson, regressor__max_depth=100, regressor__max_features=sqrt, regressor__min_samples_leaf=6, regressor__min_samples_split=4, scaler=passthrough;, score=-0.252 total time=   0.0s
[CV 5/5] END regressor=DecisionTreeRegressor(random_state=42), regressor__criterion=poisson, regressor__max_depth=100, regressor__max_features=sqrt, regressor__min_samples_leaf=6, regressor__min_samples_sp

[CV 4/5] END regressor=DecisionTreeRegressor(random_state=42), regressor__criterion=poisson, regressor__max_depth=100, regressor__max_features=sqrt, regressor__min_samples_leaf=6, regressor__min_samples_split=6, scaler=StandardScaler();, score=-0.252 total time=   0.0s
[CV 5/5] END regressor=DecisionTreeRegressor(random_state=42), regressor__criterion=poisson, regressor__max_depth=100, regressor__max_features=sqrt, regressor__min_samples_leaf=6, regressor__min_samples_split=6, scaler=StandardScaler();, score=-0.192 total time=   0.0s
[CV 1/5] END regressor=DecisionTreeRegressor(random_state=42), regressor__criterion=poisson, regressor__max_depth=100, regressor__max_features=sqrt, regressor__min_samples_leaf=6, regressor__min_samples_split=6, scaler=Normalizer();, score=-0.362 total time=   0.0s
[CV 2/5] END regressor=DecisionTreeRegressor(random_state=42), regressor__criterion=poisson, regressor__max_depth=100, regressor__max_features=sqrt, regressor__min_samples_leaf=6, regressor__min

GridSearchCV(cv=5,
             estimator=Pipeline(memory=Memory(location=outputs//cache/joblib),
                                steps=[('scaler', StandardScaler()),
                                       ('regressor', LinearRegression())]),
             param_grid=[{'regressor': [LinearRegression()],
                          'scaler': ['passthrough', StandardScaler(),
                                     Normalizer()]},
                         {'regressor': [Lasso(max_iter=2000, random_state=42,
                                              tol=0.001)],
                          'regressor__alpha': array([1.e-03,...
                                                   'friedman_mse',
                                                   'absolute_error',
                                                   'poisson'],
                          'regressor__max_depth': array([None, 10, 20, 30, 40, 50, 60, 70, 80, 90, 100], dtype=object),
                          'regressor__max_features': [None, 'sqrt'],
                          'regressor__min_samples_leaf': array([3, 4, 5, 6]),
                          'regressor__min_samples_split': array([3, 4, 5, 6]),
                          'scaler': ['passthrough', StandardScaler(),
                                     Normalizer()]}],
             scoring=make_scorer(r2_score), verbose=4)

### Results

In [33]:
pd.DataFrame(grid_search.cv_results_)

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
0          0.002709      0.002620         0.000302        0.000161   
1          0.007364      0.001528         0.000259        0.000023   
2          0.005762      0.000262         0.000268        0.000011   
3          0.003068      0.000496         0.000194        0.000011   
4          0.002460      0.000181         0.000254        0.000035   
...             ...           ...              ...             ...   
4432       0.005223      0.000141         0.000298        0.000016   
4433       0.005104      0.000184         0.000358        0.000050   
4434       0.003847      0.000114         0.000223        0.000007   
4435       0.005298      0.000155         0.000318        0.000015   
4436       0.004928      0.000209         0.000338        0.000008   

                                       param_regressor      param_scaler  \
0                                   LinearRegression()       passthrough   
1                                   LinearRegression()  StandardScaler()   
2                                   LinearRegression()      Normalizer()   
3     Lasso(max_iter=2000, random_state=42, tol=0.001)       passthrough   
4     Lasso(max_iter=2000, random_state=42, tol=0.001)  StandardScaler()   
...                                                ...               ...   
4432            DecisionTreeRegressor(random_state=42)  StandardScaler()   
4433            DecisionTreeRegressor(random_state=42)      Normalizer()   
4434            DecisionTreeRegressor(random_state=42)       passthrough   
4435            DecisionTreeRegressor(random_state=42)  StandardScaler()   
4436            DecisionTreeRegressor(random_state=42)      Normalizer()   

     param_regressor__alpha param_regressor__C param_regressor__loss  \
0                       NaN                NaN                   NaN   
1                       NaN                NaN                   NaN   
2                       NaN                NaN                   NaN   
3                     0.001                NaN                   NaN   
4                     0.001                NaN                   NaN   
...                     ...                ...                   ...   
4432                    NaN                NaN                   NaN   
4433                    NaN                NaN                   NaN   
4434                    NaN                NaN                   NaN   
4435                    NaN                NaN                   NaN   
4436                    NaN                NaN                   NaN   

     param_regressor__gamma  ... param_regressor__min_samples_split  \
0                       NaN  ...                                NaN   
1                       NaN  ...                                NaN   
2                       NaN  ...                                NaN   
3                       NaN  ...                                NaN   
4                       NaN  ...                                NaN   
...                     ...  ...                                ...   
4432                    NaN  ...                                  5   
4433                    NaN  ...                                  5   
4434                    NaN  ...                                  6   
4435                    NaN  ...                                  6   
4436                    NaN  ...                                  6   

                                                 params split0_test_score  \
0     {'regressor': LinearRegression(), 'scaler': 'p...          0.041035   
1     {'regressor': LinearRegression(), 'scaler': St...          0.041035   
2     {'regressor': LinearRegression(), 'scaler': No...          0.039811   
3     {'regressor': Lasso(max_iter=2000, random_stat...          0.043099   
4     {'regressor': Lasso(max_iter=2000, random_stat...          0.046325   
...                                                 ...               ..

In [34]:
grid_search.best_estimator_

Pipeline(memory=Memory(location=outputs//cache/joblib),
         steps=[('scaler', 'passthrough'),
                ('regressor', SVR(C=0.1, max_iter=2000))])

In [35]:
os.exit()

NameError: name 'os' is not defined

In [ ]:
print(classification_report(
    ytest,
    grid_search.predict(xtest),
    digits=4,
))

### Feature Importance

In [ ]:
importance_classes = data_df.columns[1:-3]
importance_classes.values

In [ ]:
importance = grid_search.best_estimator_._final_estimator.coef_[0]

In [ ]:
feat_importances = pd.Series(importance)
feat_importances = feat_importances.reset_index().rename(columns={"index":"class", 0:"importance"}).copy()
feat_importances["class"] = importance_classes.values
feat_importances.set_index("class", inplace=True)
feat_importances.sort_values(by="importance", inplace=True, ascending=False)
feat_importances

In [ ]:
feat_importances.iloc[:20,:].plot(kind='barh',title = 'Feature Importance')

In [ ]:
feat_importances.iloc[-20:,:].plot(kind='barh',title = 'Feature Importance')